In [1]:
from datasets import load_dataset

ds = load_dataset("do-me/Eurovoc_en")
df = ds["train"].to_pandas()
df

Generating train split: 0 examples [00:00, ? examples/s]

In [4]:
df = ds["train"].to_pandas()
df

title       date  \
0       96/493/EC: Council Decision of 29 March 1996 c... 1996-03-29   
1       Proposal for a COUNCIL AND COMMISSION DECISION... 1996-03-29   
2       Proposal for a COUNCIL AND COMMISSION DECISION... 1996-03-29   
3       Amended proposal for a COUNCIL REGULATION (EC)... 1996-03-28   
4       Proposal for a COUNCIL DIRECTIVE amending Dire... 1996-03-27   
...                                                   ...        ...   
352006  Non-opposition to a notified concentration (Ca... 2023-12-04   
352007  REPORT - on the proposal for a regulation of t... 2023-12-04   
352008                     Steps in the asylum procedure. 2023-12-02   
352009                             Do you need support? : 2023-12-02   
352010  Do you fear for your safety in your country? :... 2023-12-02   

                                         eurovoc_concepts  \
0       [UNO, forest conservation, international agree...   
1       [Ukraine, accession to the European Union, coo...   
2       [EU relations, Moldova, accession to the Europ...   
3       [Antarctic Ocean, authorised catch, conservati...   
4       [case law (EU), gender equality, job access, p...   
...                                                   ...   
352006  [India, economic concentration, electric vehic...   
352007  [EU statistics, European Statistical System, d...   
352008  [asylum seeker, external border of the EU, imm...   
352009  [aid to refugees, asylum seeker, external bord...   
352010  [aid to refugees, asylum seeker, external bord...   

                                                      url lang  \
0       http://publications.europa.eu/resource/cellar/...  eng   
1       http://publications.europa.eu/resource/cellar/...  eng   
2       http://publications.europa.eu/resource/cellar/...  eng   
3       http://publications.europa.eu/resource/cellar/...  eng   
4       http://publications.europa.eu/resource/cellar/...  eng   
...                                                   ...  ...   
352006  http://publications.europa.eu/resource/cellar/...  eng   
352007  http://publications.europa.eu/resource/cellar/...  eng   
352008  http://publications.europa.eu/resource/cellar/...  eng   
352009  http://publications.europa.eu/resource/cellar/...  eng   
352010  http://publications.europa.eu/resource/cellar/...  eng   

                                   formats  \
0       [fmx4, html, pdfa1b, print, xhtml]   
1                                    [pdf]   
2                                    [pdf]   
3               [html, pdf, pdfa1b, print]   
4               [html, pdf, pdfa1b, print]   
...                                    ...   
352006               [fmx4, pdfa2a, xhtml]   
352007                               [URI]   
352008                 [pdf, pdfx4, print]   
352009                               [pdf]   
352010                 [pdf, pdfx4, print]   

                                                     text  __index_level_0__  
0       L_1996208EN. 01000101. xml 17. 8. 1996    EN O...                 29  
1       COMMISSION OI l l ll I UKOIM AN COMMUNIMI S Br...                 48  
2       , * ir ; COMMISSION OF THE EUROPEAN COMMUNITIE...                 54  
3       COMMISSION OF THE bUROPEAN COMMUNITIES Brussel...                 73  
4       COMMISSION OF THE EUROPEAN COMMUNITIES Brussel...                108  
...                                                   ...                ...  
352006  C_202301503EN. 000101. fmx. xml Official Journ...              21936  
352007                                               None              21940  
352008  Steps in the asylum procedure Arrival 1 Applyi...              21945  
352009  Do you need support? lleuaa EUROPEAN UNION AGE...              21946  
352010  Do you fear for your safety in your country? T...              21947  

[352011 rows x 8 columns]

In [6]:
from datasets import load_dataset
from model2vec import StaticModel

model = StaticModel.from_pretrained("minishlab/M2V_base_output")

In [8]:
df["text"] = df["text"].fillna("")

In [9]:
%%time 
embeddings = model.encode(df.text)
df["embeddings"] = embeddings.tolist()

CPU times: user 17min 49s, sys: 16.3 s, total: 18min 6s
Wall time: 1min 36s


In [19]:
del df["__index_level_0__"]

In [28]:
del df["cos_sim"]

In [30]:
df = df.sort_index()

In [31]:
df.to_parquet("CELLAR_EN_16_05_2024.parquet")

## Test query

In [ ]:
from model2vec import StaticModel

model = StaticModel.from_pretrained("minishlab/M2V_base_output")

In [24]:
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity  

query = "social democracy"
quer_emb = model.encode(query)

embeddings_matrix = np.stack(df['embeddings'].to_numpy())
df["cos_sim"] = cosine_similarity(embeddings_matrix, quer_emb.reshape(1, -1))[:, 0]
df = df.sort_values("cos_sim", ascending=False)

In [26]:
df.head(5)

title       date  \
295413   10 trends shaping democracy in a volatile world. 2019-11-21   
351006                              Defence of democracy. 2023-12-20   
314572            EU citizenship report 2020 : factsheet. 2021-04-20   
286936  Opinion of the European Economic and Social Co... 2019-03-20   
330997  Making participatory and deliberative democrac... 2022-06-16   

                                         eurovoc_concepts  \
295413  [democracy, digital technology, election, popu...   
351006  [action programme, civic engagement, democracy...   
314572  [European citizenship, European election, acce...   
286936  [Liberalism, civil society, democracy, extremi...   
330997  [EU research policy, green economy, innovation...   

                                                      url lang  \
295413  http://publications.europa.eu/resource/cellar/...  eng   
351006  http://publications.europa.eu/resource/cellar/...  eng   
314572  http://publications.europa.eu/resource/cellar/...  eng   
286936  http://publications.europa.eu/resource/cellar/...  eng   
330997  http://publications.europa.eu/resource/cellar/...  eng   

                      formats  \
295413                  [pdf]   
351006                  [pdf]   
314572                  [pdf]   
286936  [fmx4, pdfa2a, xhtml]   
330997                  [pdf]   

                                                     text  \
295413  31 October 2019 10 TRENDS SHAPING DEMOCRACY IN...   
351006  Defence of Democracy #EUDemocracy 12 December ...   
314572  EU Citizenship Report 2020 F A C T S H E E T 1...   
286936  C_2019228EN. 01002401. xml 5. 7. 2019    EN Of...   
330997  #HorizonEU June 2022 MAKING PARTICIPATORY AND ...   

                                               embeddings   cos_sim  
295413  [-0.7749167680740356, 5.183741569519043, -4.15...  0.497865  
351006  [-0.4795585572719574, 6.859988212585449, -5.87...  0.451415  
314572  [-0.9046934247016907, 5.682852745056152, -4.97...  0.432170  
286936  [-0.5640900135040283, 3.6944658756256104, -4.5...  0.420833  
330997  [-0.27760544419288635, 5.397331237792969, -5.9...  0.419882